#Project - Finding Optimal Neighborhood for Opening New Restaurant


## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening a ** new restaurant** in **New Delhi**, India.

Since there are lots of restaurants in New Delhi we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with few restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Italian restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Foursquare Maps API reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of New Delhi center will be obtained using **Foursquare Maps API geocoding** of well known New Delhi location (Connaught Place)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around Connaught Place New Delhi.

Let's first find the latitude & longitude of Connaught Place New Delhi, using specific, well known address and Foursquare geocoding API.

In [0]:
# CLIENT_ID='BX20VV3N2A13OKLUHX22M521V430FHFZFFIET01JWMBPRO5A'
# CLIENT_SECRET='DDAIOS44L1V01PJL0VUIM2QZZX05SQOBJYFVUICZCVSGLPNN'
CLIENT_ID = 'YTUW3UZE5ELRNZMYY12QYXVSZVULFBBL3HJWFJA0YRA2OD55' # your Foursquare ID
CLIENT_SECRET = 'KMO3XQIQCPLS5U4CR3JUXFKGKYAOZCUVC3TY1S242VJQQ4PV' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30

In [2]:
import requests
from geopy.geocoders import Nominatim

def get_coordinates(address):#api_key,  verbose=False):
    try:
        # url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        # response = requests.get(url).json()
        # if verbose:
        #     print('Google Maps API JSON result =>', response)
        # results = response['results']
        # geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        geolocator = Nominatim(user_agent='KrGaurav')
        location = geolocator.geocode(address)
        lat = location.latitude
        lon = location.longitude
        # lat = geographical_data['lat']
        # lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
    
address = 'Connaught Place,New Delhi, India'
delhi_center = get_coordinates(address)
print('Coordinate of {}: {}'.format(address, delhi_center))

Coordinate of Connaught Place,New Delhi, India: [28.6313827, 77.2197924]


In [3]:
!pip install shapely
!pip install pyproj

     |████████████████████████████████| 10.1MB 2.8MB/s 


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Connaught Place New Delhi. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [4]:
import shapely.geometry
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Delhi center longitude={}, latitude={}'.format(delhi_center[1], delhi_center[0]))
x, y = lonlat_to_xy(delhi_center[1], delhi_center[0])
print('Delhi center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Delhi center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Delhi center longitude=77.2197924, latitude=28.6313827
Delhi center UTM X=7113946.582773518, Y=5500381.772907261
Delhi center longitude=77.21979239999885, latitude=28.631382700001293


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [5]:
delhi_center_x, delhi_center_y = lonlat_to_xy(delhi_center[1], delhi_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = delhi_center_x - 6000
x_step = 600
y_min = delhi_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(delhi_center_x, delhi_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [0]:
#!pip install folium

import folium

In [7]:
map_delhi = folium.Map(location=delhi_center, zoom_start=13)
folium.Marker(delhi_center, popup='Connaught Place').add_to(map_delhi)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_berlin) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_delhi)
    #folium.Marker([lat, lon]).add_to(map_berlin)
map_delhi

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Connaught Place New Delhi.

Let's now use Foursquare Maps API to get approximate addresses of those locations.

In [8]:
def get_address(CLIENT_ID,CLIENT_SECRET,VERSION,LIMIT, latitude, longitude, verbose=False):
    try:
        # url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION,500, LIMIT)
        response = requests.get(url).json()
        if verbose:
            print('Maps API JSON result =>', response)
        results = response['response']['venues']
        address = results[0]['location']['formattedAddress']
        return address
        # response = requests.get(url).json()
        # if verbose:
        #     print('Google Maps API JSON result =>', response)
        # results = response['results']
        # address = results[0]['formatted_address']
        #return address
    except:
        return None

addr = get_address(CLIENT_ID,CLIENT_SECRET,VERSION,LIMIT, delhi_center[0], delhi_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(delhi_center[0], delhi_center[1], addr))

Reverse geocoding check
-----------------------
Address of [28.6313827, 77.2197924] is: ['New Delhi 110001', 'Delhi', 'India']


In [9]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(CLIENT_ID,CLIENT_SECRET,VERSION,LIMIT,lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    # address = address.replace(', India', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [10]:
ad = addresses.copy()
for i in range(len(ad)):
  ad[i] = ad[i][:-1]
  ad[i] = ', '.join(ad[i])

ad[150:170]

['Delhi High Court, New Delhi. (Delhi High Court, New Delhi.), New Delhi, Delhi',
 'Mathura Road (Near Delhi Zoo), New Delhi, Delhi',
 '11 Sunder Nagar, New Delhi, Delhi',
 'Karol Bagh, New Delhi, Delhi',
 '1749/55 Naiwala, Karol Bagh, New Delhi, Delhi',
 'New Link Rd (Ridge Rd), New Delhi 110005, Delhi',
 'Jhandewalan (Dr Bhim Rao Ambedkar Marg), New Delhi 110005, Delhi',
 'Ramakrishna Ashram, New Delhi, Delhi',
 'Ramakrishna Ashram, New Delhi, Delhi',
 '7A Doctor Lane, New Delhi 110001, Delhi',
 'Connaught Place, New Delhi, Delhi',
 'Baba Kharak Singh Marg (Connaught Place), New Delhi 110001, Delhi',
 'Connaught Place, New Delhi, Delhi',
 '',
 '3, Kasturba Gandhi Marg, New Delhi, Delhi',
 '3, Kasturba Gandhi Marg, New Delhi, Delhi',
 '',
 'Kasturba Gandhi Marg, New Delhi 110001, Delhi',
 'New Delhi, Delhi',
 'Pragati Maidan, New Delhi, Delhi']

Looking good. Let's now place all this into a Pandas dataframe.

In [11]:
addresses[150:170]

[['Delhi High Court, New Delhi. (Delhi High Court, New Delhi.)',
  'New Delhi',
  'Delhi',
  'India'],
 ['Mathura Road (Near Delhi Zoo)', 'New Delhi', 'Delhi', 'India'],
 ['11 Sunder Nagar', 'New Delhi', 'Delhi', 'India'],
 ['Karol Bagh', 'New Delhi', 'Delhi', 'India'],
 ['1749/55 Naiwala, Karol Bagh', 'New Delhi', 'Delhi', 'India'],
 ['New Link Rd (Ridge Rd)', 'New Delhi 110005', 'Delhi', 'India'],
 ['Jhandewalan (Dr Bhim Rao Ambedkar Marg)',
  'New Delhi 110005',
  'Delhi',
  'India'],
 ['Ramakrishna Ashram', 'New Delhi', 'Delhi', 'India'],
 ['Ramakrishna Ashram', 'New Delhi', 'Delhi', 'India'],
 ['7A Doctor Lane', 'New Delhi 110001', 'Delhi', 'India'],
 ['Connaught Place', 'New Delhi', 'Delhi', 'India'],
 ['Baba Kharak Singh Marg (Connaught Place)',
  'New Delhi 110001',
  'Delhi',
  'India'],
 ['Connaught Place', 'New Delhi', 'Delhi', 'India'],
 ['India'],
 ['3, Kasturba Gandhi Marg', 'New Delhi', 'Delhi', 'India'],
 ['3, Kasturba Gandhi Marg', 'New Delhi', 'Delhi', 'India'],
 ['In

In [12]:
import pandas as pd

df_locations = pd.DataFrame({'Address': ad,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

# df_locations.head(5)
len(df_locations['Address'])

364

In [0]:
# df_locations = df_locations[df_locations['Address']!=''] 
# df_locations.head(25)
df_locations.to_pickle('./locations.pkl') #...and let's now save/persist this data into local file.

In [0]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

restaurant_categories = ['54135bf5e4b08f3d2429dfe2','54135bf5e4b08f3d2429dff3','54135bf5e4b08f3d2429dff5',
                                 '54135bf5e4b08f3d2429dff2','54135bf5e4b08f3d2429dfe1','54135bf5e4b08f3d2429dfe3',
                                 '54135bf5e4b08f3d2429dfe9','54135bf5e4b08f3d2429dfe6','54135bf5e4b08f3d2429dfdf',
                                 '54135bf5e4b08f3d2429dfe4','54135bf5e4b08f3d2429dfe7','54135bf5e4b08f3d2429dff4',
                                 '54135bf5e4b08f3d2429dfe0','54135bf5e4b08f3d2429dfdd','54135bf5e4b08f3d2429dff6',
                                 '54135bf5e4b08f3d2429dff0','54135bf5e4b08f3d2429dff1','54135bf5e4b08f3d2429dfde',
                                 '54135bf5e4b08f3d2429dfec','54135bf5e4b08f3d2429dfef','4bf58dd8d48988d120951735',
                                 '4bf58dd8d48988d16e941735','4bf58dd8d48988d147941735','4bf58dd8d48988d1e0931735',
                                 '4bf58dd8d48988d128941735','4bf58dd8d48988d16a941735','4bf58dd8d48988d1d0941735']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'hotel', 'bhandar','bhojnalaya','wale','shop','house']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        # if 'fast food' in category_name:
        #     restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    # address = address.replace(', Deutschland', '')
    # address = address.replace(', Germany', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [17]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    i_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, CLIENT_ID,CLIENT_SECRET, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_indian = is_restaurant(venue_categories, specific_filter=restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_indian, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_indian:
                    i_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, i_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
i_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('i_restaurants_350.pkl', 'rb') as f:
        i_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, i_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('italian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(i_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
        

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [18]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Indian restaurants:', len(i_restaurants))
print('Percentage of Indian restaurants: {:.2f}%'.format(len(i_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 317
Total number of Indian restaurants: 81
Percentage of Indian restaurants: 25.55%
Average number of restaurants in neighborhood: 1.6456043956043955


In [19]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('51c331da498ef765a5b427d9', "McDonald's", 28.612620416424136, 77.18988371221602, 'India', 298, True, 7112752.653784067, 5494813.256361888)
('53981584498e8b3006bf250e', 'Oriental Lounge', 28.5981741444177, 77.20460635312018, 'India', 282, False, 7116154.290578338, 5494481.572116371)
('4bbdfc7c8a4fb71386a23d9d', 'Sevilla', 28.60114350202022, 77.21617449259902, 'The Claridges Hotel (12 Aurangzeb Rd), New Delhi, Delhi, India', 118, False, 7117126.468986579, 5496079.950845044)
('4d974c720caaa143ac4b8eb3', 'Dhaba by Claridges', 28.600633368284306, 77.21655356969086, '12 Aurangzeb Rd (Motilal Nehru Marg), New Delhi 110011, Delhi, India', 108, True, 7117230.508048079, 5496053.508217669)
('4fd9f90ae4b0a04895bb04b3', 'Jade', 28.600383802307814, 77.21678961059109, '12 Aurangzeb Road, New Delhi, Delhi, India', 115, False, 7117287.20030896, 5496045.878006362)
('54a80f35498ec12f9dd4b255', 'Ye Old Bakery', 28.601071, 77.216086, 'India', 319, True, 7117

In [20]:
print('List of Indian restaurants')
print('---------------------------')
for r in list(i_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(i_restaurants))

List of Indian restaurants
---------------------------
('51c331da498ef765a5b427d9', "McDonald's", 28.612620416424136, 77.18988371221602, 'India', 298, True, 7112752.653784067, 5494813.256361888)
('4d974c720caaa143ac4b8eb3', 'Dhaba by Claridges', 28.600633368284306, 77.21655356969086, '12 Aurangzeb Rd (Motilal Nehru Marg), New Delhi 110011, Delhi, India', 108, True, 7117230.508048079, 5496053.508217669)
('54a80f35498ec12f9dd4b255', 'Ye Old Bakery', 28.601071, 77.216086, 'India', 319, True, 7117124.950290259, 5496061.261175161)
('56ec385fcd10a1d58054a8ce', "Nzn'ın Mutfağı", 28.613466, 77.20854, 'Yeni Mah, India', 246, True, 7114788.092027564, 5496878.2361330325)
('5447b8b6498e04004ec5be5d', 'SODABOTTLEOPENERWALA', 28.600140869804918, 77.22627303643019, 'Khan Market, New Delhi, Delhi, India', 163, True, 7118402.1837877715, 5497009.175626736)
('4e24769a814d32181a6f3bfb', "McDonald's", 28.600607925464374, 77.22778777419222, 'Khan Market (Lodi Estate), New Delhi 110003, Delhi, India', 332, T

In [22]:
# location_restaurants[1]
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: 
Restaurants around location 102: 
Restaurants around location 103: 
Restaurants around location 104: Geoffrey's, Bikanervala
Restaurants around location 105: 
Restaurants around location 106: U N I canteen
Restaurants around location 107: The One
Restaurants around location 108: Masala Library, eau de Monsoon, Le Belvedere, Le Meridien, The One
Restaurants around location 109: 
Restaurants around location 110: 


Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in different color.

In [23]:
map_delhi = folium.Map(location=delhi_center, zoom_start=13)
folium.Marker(delhi_center, popup='Connaught Place').add_to(map_delhi)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_indian = res[6]
    color = 'red' if is_indian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_delhi)
map_delhi

Looking good. So now we have all the restaurants in area within few kilometers from Connaught Place,New Delhi, and we know which ones are Indian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Indian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Connaught Place,New Delhi that have low restaurant density, particularly those with low number of Indian restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from Connaught Place,New Delhi**. We have also **identified Indian restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of Berlin - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general & focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [24]:
location_restaurants_count = [len(res) for res in location_restaurants]
# len(location_restaurants_count)
# len(df_locations['Address'])
df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 1.6456043956043955


Address  ...  Restaurants in area
0  Rashtrapati Bhawan, President's Estate, New De...  ...                    0
1  Mother Teressa Crescent,, New Delhi 110011, Delhi  ...                    1
2  Mother Teressa Crescent,, New Delhi 110011, Delhi  ...                    0
3  Mother Teressa Crescent,, New Delhi 110011, Delhi  ...                    0
4                  Teen Murti Road, New Delhi, Delhi  ...                    0
5                  Teen Murti Road, New Delhi, Delhi  ...                    0
6                  Teen Murti Road, New Delhi, Delhi  ...                    1
7                                                     ...                    0
8              Talkatora Rd, New Delhi 110004, Delhi  ...                    0
9  Rashtrapati Bhawan, President's Estate, New De...  ...                    0

[10 rows x 7 columns]

OK, now let's calculate the **distance to nearest restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [0]:
distances_to_indian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in i_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_indian_restaurant.append(min_distance)

df_locations['Distance to Indian restaurant'] = distances_to_indian_restaurant

In [26]:
df_locations.head(10)

Address  ...  Distance to Indian restaurant
0  Rashtrapati Bhawan, President's Estate, New De...  ...                     623.702623
1  Mother Teressa Crescent,, New Delhi 110011, Delhi  ...                     147.376217
2  Mother Teressa Crescent,, New Delhi 110011, Delhi  ...                     611.910563
3  Mother Teressa Crescent,, New Delhi 110011, Delhi  ...                    1202.975197
4                  Teen Murti Road, New Delhi, Delhi  ...                    1799.962253
5                  Teen Murti Road, New Delhi, Delhi  ...                    2241.089273
6                  Teen Murti Road, New Delhi, Delhi  ...                    1961.284306
7                                                     ...                    1551.420294
8              Talkatora Rd, New Delhi 110004, Delhi  ...                     979.601815
9  Rashtrapati Bhawan, President's Estate, New De...  ...                     482.010895

[10 rows x 8 columns]

In [27]:
print('Average distance to closest Indain restaurant from each area center:', df_locations['Distance to Indian restaurant'].mean())

Average distance to closest Indain restaurant from each area center: 925.6867551693259


OK, so **on average Indian restaurant can be found within ~1000m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show **borders of New Delhi** on our map and a few circles indicating distance of 1km, 2km and 3km from Connaught Place,New Delhi.

In [0]:
# delhi_boroughs_url = 'https://raw.githubusercontent.com/m-hoerz/berlin-shapes/master/berliner-bezirke.geojson'
# delhi_boroughs = requests.get(delhi_boroughs_url).json()

# def boroughs_style(feature):
#     return { 'color': 'blue', 'fill': False }

In [0]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

indian_latlons = [[res[2], res[3]] for res in i_restaurants.values()]

In [31]:
from folium import plugins
from folium.plugins import HeatMap

map_delhi = folium.Map(location=delhi_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_delhi) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_delhi)
# folium.Marker(delhi_center).add_to(map_delhi)
folium.Marker(delhi_center, popup='Connaught Place').add_to(map_delhi)
folium.Circle(delhi_center, radius=1000, fill=False, color='white').add_to(map_delhi)
folium.Circle(delhi_center, radius=2000, fill=False, color='white').add_to(map_delhi)
folium.Circle(delhi_center, radius=3000, fill=False, color='white').add_to(map_delhi)
# folium.GeoJson(delhi_boroughs, style_function=boroughs_style, name='geojson').add_to(map_delhi)
map_delhi

 
Let's create another heatmap map showing **heatmap/density of Indian restaurants** only.

In [32]:
map_delhi = folium.Map(location=delhi_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_delhi) #cartodbpositron cartodbdark_matter
HeatMap(indian_latlons).add_to(map_delhi)
# folium.Marker(delhi_center).add_to(map_delhi)
folium.Marker(delhi_center, popup='Connaught Place').add_to(map_delhi)
folium.Circle(delhi_center, radius=1000, fill=False, color='white').add_to(map_delhi)
folium.Circle(delhi_center, radius=2000, fill=False, color='white').add_to(map_delhi)
folium.Circle(delhi_center, radius=3000, fill=False, color='white').add_to(map_delhi)
# folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_delhi)
map_delhi

This map is not so 'hot' (Italian restaurants represent a subset of ~30% of all restaurants in New Delhi).

Based on this we will now focus our analysis on areas *south-west, south, south-east and east from Connaught Place,New Delhi* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**. This places our location candidates mostly in boroughs **Chandni chowk** 

In [33]:
roi_x_min = delhi_center_x - 2000
roi_y_max = delhi_center_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_delhi = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_delhi)
folium.Marker(delhi_center).add_to(map_delhi)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_delhi)
# folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_delhi)
map_delhi

Not bad - this nicely covers all the pockets of low restaurant density in old delhi closest to New delhi center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [34]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Indian restaurant**.

In [36]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_indian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, i_restaurants)
    roi_indian_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [40]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Indian restaurant':roi_indian_distances})

df_roi_locations.head(10)

Latitude  Longitude  ...  Restaurants nearby  Distance to Indian restaurant
0  28.612888  77.204520  ...                   0                     632.261995
1  28.612504  77.204995  ...                   0                     575.719880
2  28.615362  77.202283  ...                   0                    1026.852208
3  28.614978  77.202759  ...                   0                     936.014747
4  28.614595  77.203234  ...                   0                     847.243622
5  28.614211  77.203709  ...                   0                     761.262047
6  28.613827  77.204184  ...                   0                     679.130366
7  28.613443  77.204659  ...                   0                     602.425267
8  28.613059  77.205134  ...                   0                     533.492598
9  28.612675  77.205609  ...                   0                     475.723135

[10 rows x 6 columns]

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Indian restaurants in radius of 400 meters**.

In [42]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to Indian restaurant']>=400)
print('Locations with no Indian restaurants within 400m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 1934
Locations with no Indian restaurants within 400m: 1710
Locations with both conditions met: 1627


Let's see how this looks on a map.

In [43]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_delhi = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_delhi)
HeatMap(restaurant_latlons).add_to(map_delhi)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_delhi)
folium.Marker(delhi_center).add_to(map_delhi)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_delhi) 
# folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_delhi

Let's now show those good locations in a form of heatmap:

In [44]:
map_delhi = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_delhi)
folium.Marker(delhi_center).add_to(map_delhi)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_delhi)
# folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_delhi

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Indian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [55]:
from sklearn.cluster import KMeans

number_of_clusters = 10

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_delhi = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_delhi)
HeatMap(restaurant_latlons).add_to(map_delhi)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_delhi)
folium.Marker(delhi_center).add_to(map_delhi)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_delhi) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_delhi)
# folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_delhi)
map_delhi

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [56]:
map_delhi = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(delhi_center).add_to(map_delhi)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_delhi)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_delhi)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_delhi) 
# folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_delhi)
map_delhi

In [48]:
map_delhi = folium.Map(location=[28.6562654,77.2299093], zoom_start=15)
folium.Marker(delhi_center).add_to(map_delhi)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_delhi) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_delhi)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_delhi)
# folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_delhi)
map_delhi

In [0]:
# map_delhi = folium.Map(location=[52.516347, 13.428403], zoom_start=15)
# folium.Marker(delhi_center).add_to(map_delhi)
# for lon, lat in cluster_centers:
#     folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_delhi) 
# for lat, lon in zip(good_latitudes, good_longitudes):
#     folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_delhi)
# for lat, lon in zip(good_latitudes, good_longitudes):
#     folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_delhi)
# folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_delhi)
# map_delhi

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [54]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(CLIENT_ID,CLIENT_SECRET,VERSION,LIMIT, lat, lon)
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, delhi_center_x, delhi_center_y)
    print('{}{} => {:.1f}km from Connaught'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

['New Delhi', 'Delhi', 'India']                                                => 3.3km from Connaught
['Sansad Marg, Connaught Place', 'New Delhi 110001', 'Delhi', 'India']                                               => 1.4km from Connaught
['Shop No 3, North Avenue (MP Market)', 'New Delhi', 'Delhi', 'India']                                               => 3.2km from Connaught
['3, Kasturba Gandhi Marg', 'New Delhi', 'Delhi', 'India']                                               => 1.5km from Connaught
['New Delhi', 'New Delhi 110001', 'ND', 'India']                                               => 3.6km from Connaught
['India']                                                  => 2.5km from Connaught
['Parliament Street', 'Delhi 110001', 'Delhi', 'India']                                               => 2.3km from Connaught
['India']                                                  => 2.7km from Connaught
['Bangla Sa

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (all less than 4km from Cannaught Place, and about half of those less than 2km from Cannaught Place). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations.

In [0]:
# map_delhi = folium.Map(location=roi_center, zoom_start=14)
# folium.Circle(delhi_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_delhi)
# for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
#     folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_delhi) 
# for lat, lon in zip(good_latitudes, good_longitudes):
#     folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_delhi)
# map_delhi

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Delhi areas close to center with low number of restaurants in order to aid stakeholders in narrowing down the search for optimal location for a new restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis, and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.